In [25]:
from cortano import RemoteInterface
from ultralytics import YOLO
import numpy as np
import cv2
import cv2
import numpy as np
import time
import pygame
import sys
from lan import lan

model = YOLO("yolov8s.pt")
lan.stop()

In [26]:
m = [0] * 10
lan.write(m)

In [27]:
lan.stop()
lan.start("10.0.0.119", 9999, frame_shape=(360, 640))
m = [0] * 10
lan.write(m)
print(lan.read())
lan.write(m)
print(lan.read())

[39.60043406486511, 3811, 0, 0]
[39.60043406486511, 3811, 0, 0]


In [28]:
print(lan.read())

[0.2861659526824951, 3852, 0, 0]


In [29]:


ball_should_be_within_bbox = (299,259,377,341)
h = ball_should_be_within_bbox[2]-ball_should_be_within_bbox[0]
w = ball_should_be_within_bbox[3]-ball_should_be_within_bbox[1]
ball_should_be_within = (ball_should_be_within_bbox[0], ball_should_be_within_bbox[1], h, w)

motor_vals = [0] * 10
sensor_vals = np.zeros((20,), np.int32)
pygame.init()
                                  # w, h
screen = pygame.display.set_mode((640, 360))
clock = pygame.time.Clock()
screen.fill((63, 63, 63))

def decode_depth_frame(f):
    if f.ndim == 2:
        print('Something is wrong with the pyrealsense, quitting')
        pygame.quit()
        lan.stop()
        sys.exit(0)
    R = np.left_shift(frame[:, :, 0].astype(np.uint16), 5)
    G = frame[:, :, 1].astype(np.uint16)
    B = np.left_shift(frame[:, :, 2].astype(np.uint16), 5)
    I = np.bitwise_or(R, G, B)
    return I
    
def bb_intersection_over_union(boxA, boxB):
	# determine the (x, y)-coordinates of the intersection rectangle
	xA = max(boxA[0], boxB[0])
	yA = max(boxA[1], boxB[1])
	xB = min(boxA[2], boxB[2])
	yB = min(boxA[3], boxB[3])
	# compute the area of intersection rectangle
	interArea = max(0, xB - xA + 1) * max(0, yB - yA + 1)
	# compute the area of both the prediction and ground-truth
	# rectangles
	boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
	boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
	# compute the intersection over union by taking the intersection
	# area and dividing it by the sum of prediction + ground-truth
	# areas - the interesection area
	iou = interArea / float(boxAArea + boxBArea - interArea)
	# return the intersection over union value
	return iou
    
def get_midpoint(boxA):
    width = abs(boxA[0] - boxA[2])
    height = abs(boxA[1] - boxA[3])
    mid_point = (int(boxA[0]+(width/2)), int(boxA[1]+(height/2)))
    return mid_point

mp_target = get_midpoint(ball_should_be_within_bbox)
print(f'MP  REF BOX {mp_target}')


keys_letters = {k[2:]: 0 for k in dir(pygame) if k.startswith("K_")}
key_number_mappings={}
for key in keys_letters.keys():
    key_number_mappings[getattr(pygame, f"K_{key}")] = key
    
""" 
keys_letters={'a':0, 'w':0, 's':0, 'd':0, 'UP':0, 'DOWN':0, 'LEFT':0, 'RIGHT':0, 'q':0}


key_number_mappings={
    97: 'a',
    119: 'w',
    115: 's',
    100: 'd',
    1073741906: 'UP', 
    1073741905: 'DOWN',
    1073741904: 'LEFT',
    1073741903: 'RIGHT',
    113: 'q'
}
"""

MP  REF BOX (338, 300)


" \nkeys_letters={'a':0, 'w':0, 's':0, 'd':0, 'UP':0, 'DOWN':0, 'LEFT':0, 'RIGHT':0, 'q':0}\n\n\nkey_number_mappings={\n    97: 'a',\n    119: 'w',\n    115: 's',\n    100: 'd',\n    1073741906: 'UP', \n    1073741905: 'DOWN',\n    1073741904: 'LEFT',\n    1073741903: 'RIGHT',\n    113: 'q'\n}\n"

In [30]:
pickup_ball = 0
while True:
    for event in pygame.event.get():
        if event.type == pygame.QUIT: 
            motor_vals = [0] * 10
            lan.write(motor_vals)
            pygame.quit()
            lan.stop()
            sys.exit(0)
        elif event.type == pygame.KEYDOWN:
            print(f'pressed {key_number_mappings[event.key]}')
            keys_letters[key_number_mappings[event.key]] = 1
        elif event.type == pygame.KEYUP:
            print(f'released {key_number_mappings[event.key]}')
            keys_letters[key_number_mappings[event.key]] = 0 

    color_image,depth_image = lan.get_frame()
    
    #color_image , depth = frame[:,:640], frame[:,640:]
    #depth_image = decode_depth_frame(depth)
    
    disp_img = np.swapaxes(np.flip(color_image, axis=-1), 0, 1)
    surf = pygame.surfarray.make_surface(disp_img)
    import time
    start = time.time()
    result = model(color_image, verbose=False)[0]
    end = time.time()
    bboxes = np.array(result.boxes.xyxy.cpu(), dtype="int")
    classes = np.array(result.boxes.cls.cpu(), dtype="int")
    if pickup_ball == 0:
        for cls, bbox in zip(classes, bboxes):
            #if cls in (29,32,47,49,54):
            if cls == 32:
                (x, y, x2, y2) = bbox
                width = abs(x-x2)
                height = abs(y-y2)
                pygame.draw.rect(surf, (255,0,0), pygame.Rect(x, y, width, height), 3)
                mid_point = (int(x+(width/2)), int(y+(height/2)))
                distance = depth_image[mid_point[1]][mid_point[0]]/10
                txt = f'{result.names[cls]} - {distance}cm'
                iou = bb_intersection_over_union(ball_should_be_within_bbox, bbox)
                mp_target = get_midpoint(ball_should_be_within_bbox)
                mp_current = get_midpoint(bbox)
                  
                if iou <= 0.75:
                    if iou > 0.4:
                        print(f'Iou :  {iou}')
                    if abs(mp_current[0] - mp_target[0]) <= 5:
                        if mp_current[1] > mp_target[1]:
                            keys_letters["RIGHT"] = 0
                            keys_letters["LEFT"] = 0
                            keys_letters["UP"] = 0
                            keys_letters["DOWN"] = 1
                        elif mp_current[1] < mp_target[1]:
                            keys_letters["RIGHT"] = 0
                            keys_letters["LEFT"] = 0
                            keys_letters["UP"] = 1
                            keys_letters["DOWN"] = 0                
                    elif mp_current[0] > mp_target[0]:
                        keys_letters["RIGHT"] = 1
                        keys_letters["LEFT"] = 0
                        keys_letters["UP"] = 0
                        keys_letters["DOWN"] = 0
                    elif mp_current[0] < mp_target[0]:
                        keys_letters["RIGHT"] = 0
                        keys_letters["LEFT"] = 1
                        keys_letters["UP"] = 0
                        keys_letters["DOWN"] = 0
    
                else:
                    print(f'Crossed trhesohld : {iou}')
                    #keys_letters["q"] = 1
                    pickup_ball = 1
                    keys_letters["LEFT"] = 0
                    keys_letters["RIGHT"] = 0
                    keys_letters["UP"] = 0
                    keys_letters["DOWN"] = 0
                  
    turning_speed = 50 #64   
    straight_speed = 40
    
    if keys_letters["UP"]: #forward      
        motor_vals[0] = -straight_speed
        motor_vals[9] = straight_speed
    elif keys_letters["DOWN"]: #reverse
        motor_vals[0] = straight_speed
        motor_vals[9] = -straight_speed
        
    elif keys_letters["LEFT"]: #left
        motor_vals[0] = turning_speed
        motor_vals[9] = turning_speed
    elif keys_letters["RIGHT"]: #right
        motor_vals[0] = -turning_speed
        motor_vals[9] = -turning_speed
        
    elif keys_letters["w"]: #up
        motor_vals[6] = base_val
    elif keys_letters["s"]: #down
        motor_vals[6] = -base_val
    elif keys_letters["a"]: #open
        motor_vals[7] = base_val
    elif keys_letters["d"]: #close
        motor_vals[7] = -base_val
    elif keys_letters["q"]:     
        motor_vals = [0] * 10
        lan.write(motor_vals)
        pygame.quit()
        lan.stop()
        sys.exit(0)
    else:
        motor_vals = [0] * 10

    lan.write(motor_vals)

    msg = lan.read()
    potentiometer_reading = msg[1]

    if color_image is not None: 
        pygame.draw.rect(surf, (0,255,0), pygame.Rect(*ball_should_be_within), 3)
        screen.blit(surf, (0,0))

    pygame.display.flip()
    import time
    if pickup_ball == 1:
        print('Picking up ball')
        motor_vals = [0] * 10
        lan.write(motor_vals)
        # BRINGN ARM DOWN
        print('Brinign arm down')
        while potentiometer_reading > 2700: #after that anyway gravity will bring it down
            msg = lan.read()
            potentiometer_reading = msg[1]
            print(f'ARM DOWN: {potentiometer_reading}')
            motor_vals[6] = -40
            lan.write(motor_vals) 
            

        motor_vals = [0] * 10
        lan.write(motor_vals)
        time.sleep(2)
        
        # CLOSE CLAW
        print('closing claw')       
        motor_vals[7] = -50
        lan.write(motor_vals)
        time.sleep(1.5)
        
        
        motor_vals = [0] * 10 
        motor_vals[7] = -10
        lan.write(motor_vals)
        time.sleep(1.5)
        
        print('arm up')
        #BRING ARM UP
        while potentiometer_reading < 3680:
            msg = lan.read()
            potentiometer_reading = msg[1]
            motor_vals[6] = 60
            lan.write(motor_vals)
            
        pickup_ball = 0
        motor_vals = [0] * 10
        motor_vals[7] = -10
        lan.write(motor_vals)
        
        #go drop it in the wall
        motor_vals[0] = -straight_speed
        motor_vals[9] = straight_speed
        lan.write(motor_vals)
        time.sleep(3)

        motor_vals = [0] * 10 
        motor_vals[7] = -10
        lan.write(motor_vals)

        while potentiometer_reading > 3400 : #after that anyway gravity will bring it down
            msg = lan.read()
            potentiometer_reading = msg[1]
            print(f'ARM DOWN: {potentiometer_reading}')
            motor_vals[6] = -10
            lan.write(motor_vals) 
            
              
        holding_voltage = 28
        motor_vals = [0] * 10
        motor_vals[6] = holding_voltage
        motor_vals[7] = -10
        lan.write(motor_vals)
        time.sleep(2.5)
        
        #open claw
        print('opening claw')       
        motor_vals[7] = 50
        lan.write(motor_vals)
        time.sleep(1)

        motor_vals = [0] * 10 
        lan.write(motor_vals)
        
        print('arm up')
        #BRING ARM UP
        while potentiometer_reading < 3680:
            msg = lan.read()
            potentiometer_reading = msg[1]
            motor_vals[6] = 60
            lan.write(motor_vals)
            
        motor_vals = [0] * 10 
        lan.write(motor_vals)
        
        pygame.quit()
        lan.stop()
        sys.exit(0)        
            
        



Iou :  0.44799612543891515
Iou :  0.4306735255413327
Iou :  0.47881510258589294
Iou :  0.5543383542885597
Iou :  0.5059589630175697
Iou :  0.44917993535256795
Iou :  0.40059790732436473
Iou :  0.46177847113884557
Iou :  0.4644030668127054
Iou :  0.42757147941630086
Iou :  0.4086966578003932
Iou :  0.4482225656877898
Iou :  0.4881505008551185
Iou :  0.4477933261571582
Iou :  0.4129239230064161
Iou :  0.506407863630708
Iou :  0.460258111204921
Iou :  0.4118751466791833
Iou :  0.42261135268539196
Iou :  0.5261345467962121
Iou :  0.5489393375511723
Iou :  0.5051278882985296
Iou :  0.4414796846573681
Iou :  0.40132805219012113
Iou :  0.4771597633136095
Iou :  0.49645390070921985
Iou :  0.5637074789617162
Iou :  0.6080639302579005
Iou :  0.7332731726182803
Crossed trhesohld : 0.8444444444444444
Picking up ball
Brinign arm down
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
ARM DOWN: 3846
AR

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



closing claw
arm up
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM DOWN: 3851
ARM D

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



opening claw
arm up


SystemExit: 0

/Users/shanmugamr/python_tests/lib/python3.10/site-packages/IPython/core/interactiveshell.py:3406: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


### 